In [14]:
import os
import numpy as np
os.chdir('/Users/gabriele/PycharmProjects/RecSys')
##Best Config is: 'topK': 192, 'l1_ratio': 0.1412276559017871, 'alpha': 0.006804121317480965, 'workers': 10

In [21]:
from src.HyperparameterTuning.SearchAbstractClass import SearchInputRecommenderArgs
from src.Recommenders.SLIM.SLIMElasticNetRecommender import MultiThreadSLIM_SLIMElasticNetRecommender
from Utils.utils import create_URM,create_ICM_with_events, combine_matrices,create_submission,write_submission
from src.Evaluation.Evaluator import EvaluatorHoldout
from src.Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample
from skopt.space import Real, Integer, Categorical

In [22]:
URM = create_URM()
ICM = create_ICM_with_events()


URM_train_validation,URM_test = split_train_in_two_percentage_global_sample(URM,train_percentage=0.85)
URM_train, URM_validation = split_train_in_two_percentage_global_sample(URM_train_validation,train_percentage=0.85)

StackedMatrices = combine_matrices(ICM=ICM, URM=URM_train)
URM_stacked = combine_matrices(ICM=ICM, URM=URM)


 56%|████████████████████▋                | 10112/18059 [06:19<03:52, 34.13it/s]

In [17]:
##SELECT 25% OF USERS WITH LONGEST PROFILES TO FINE-TUNE THE HYPERPARAMETERS
users_to_ignore=[]
profile_length = np.ediff1d(URM_train.indptr)
block_size = int(len(profile_length) * 0.25)

start_pos = 3 * block_size
end_pos = min(4 * block_size, len(profile_length))
sorted_users = np.argsort(profile_length)

users_in_group = sorted_users[start_pos:end_pos]

users_in_group_p_len = profile_length[users_in_group]
sorted_users = np.argsort(profile_length)

users_not_in_group_flag = np.isin(sorted_users, users_in_group, invert=True)

In [18]:
evaluator_test = EvaluatorHoldout(URM_test, cutoff_list=[10])
evaluator_validation = EvaluatorHoldout(URM_validation, cutoff_list=[10],ignore_users=sorted_users[users_not_in_group_flag])

EvaluatorHoldout: Ignoring 13637 ( 0.1%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 13631 ( 0.1%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 10238 Users


In [19]:
from src.HyperparameterTuning.SearchBayesianSkopt import SearchBayesianSkopt
hyperparameters_range_dictionary = {
    "topK": Integer(50,300),
    "l1_ratio": Real(0.01,1),
    "alpha": Real(0.001,0.01),
    "workers": Categorical([10])
}
recommender_input_args = SearchInputRecommenderArgs(
    CONSTRUCTOR_POSITIONAL_ARGS = [StackedMatrices],     # For a CBF model simply put [URM_train, ICM_train]
    CONSTRUCTOR_KEYWORD_ARGS = {},
    FIT_POSITIONAL_ARGS = [],
    FIT_KEYWORD_ARGS = {}
)
recommender_input_args_last_test = SearchInputRecommenderArgs(
    CONSTRUCTOR_POSITIONAL_ARGS = [URM_train_validation],     # For a CBF model simply put [URM_train_validation, ICM_train]
    CONSTRUCTOR_KEYWORD_ARGS = {},
    FIT_POSITIONAL_ARGS = [],
    FIT_KEYWORD_ARGS = {}
)

tuning_class = SearchBayesianSkopt(recommender_class=MultiThreadSLIM_SLIMElasticNetRecommender,
                                   evaluator_validation=evaluator_validation,
                                   evaluator_test=evaluator_test)

n_cases = 100
n_random_starts = n_cases*0.3
output_folder_path = "logs/"

tuning_class.search(recommender_input_args=recommender_input_args,
                    recommender_input_args_last_test=recommender_input_args_last_test,
                    hyperparameter_search_space=hyperparameters_range_dictionary,
                    metric_to_optimize="MAP",
                    cutoff_to_optimize= 10,
                    n_cases= n_cases,
                    n_random_starts=n_random_starts,
                    output_folder_path=output_folder_path,
                    output_file_name_root=MultiThreadSLIM_SLIMElasticNetRecommender.RECOMMENDER_NAME,
                    save_model="best"
                    )

Iteration No: 1 started. Evaluating function at random point.
SearchBayesianSkopt: Testing config: {'topK': 62, 'l1_ratio': 0.5247279543848352, 'alpha': 0.001341428858986418, 'workers': 10}
SLIMElasticNetRecommender: URM Detected 10245 ( 2.8%) users with no interactions.



 22%|████████▏                             | 3912/18059 [00:50<02:50, 82.79it/s]


 43%|████████████████▍                     | 7784/18059 [01:36<02:06, 81.36it/s]


 65%|███████████████████████▎            | 11688/18059 [02:21<01:03, 100.31it/s]


 87%|███████████████████████████████▏    | 15656/18059 [03:11<00:20, 117.51it/s]


...

 35%|█████████████▎                        | 6312/18059 [06:54<05:42, 34.26it/s]

 35%|█████████████▎                        | 6344/18059 [06:55<05:16, 36.99it/s]

 35%|█████████████▍                        | 6376/18059 [06:56<04:58, 39.18it/s]

 35%|█████████████▍                        | 6400/18059 [07:06<04:57, 39.18it/s]

 35%|█████████████▍                        | 6408/18059 [07:07<22:46,  8.53it/s]

 36%|█████████████▌                        | 6440/18059 [07:08<17:54, 10.81it/s]

 36%|█████████████▌                        | 6472/18059 [07:10<16:09, 11.96it/s]

 36%|█████████████▋                        | 6504/18059 [07:10<11:59, 16.07it/s]

 36%|█████████████▊                        | 6536/18059 [07:12<10:18, 18.64it/s]

 36%|█████████████▊                        | 6568/18059 [07:12<08:27, 22.66it/s]

 37%|█████████████▉                        | 6600/18059 [07:12<06:08, 31.07it/s]

 37%|██████████████                        | 6664/18059 [07:12<03:32, 53.71it/s]

 37%|███████████

 52%|███████████████████▉                  | 9480/18059 [10:09<07:23, 19.35it/s]

 53%|████████████████████                  | 9512/18059 [10:09<05:49, 24.45it/s]

 53%|████████████████████                  | 9544/18059 [10:10<04:58, 28.50it/s]

 53%|████████████████████▏                 | 9576/18059 [10:14<08:48, 16.05it/s]

 53%|████████████████████▏                 | 9608/18059 [10:22<17:15,  8.16it/s]

 53%|████████████████████▎                 | 9640/18059 [10:23<12:31, 11.20it/s]

 54%|████████████████████▎                 | 9672/18059 [10:23<09:30, 14.70it/s]

 54%|████████████████████▍                 | 9704/18059 [10:25<08:34, 16.24it/s]

 54%|████████████████████▍                 | 9736/18059 [10:28<09:42, 14.29it/s]

 54%|████████████████████▌                 | 9768/18059 [10:28<06:54, 20.02it/s]

 54%|████████████████████▌                 | 9800/18059 [10:29<06:31, 21.12it/s]

 54%|████████████████████▋                 | 9832/18059 [10:29<05:10, 26.54it/s]

 55%|███████████

 69%|█████████████████████████▋           | 12520/18059 [13:32<08:08, 11.34it/s]

 70%|█████████████████████████▋           | 12552/18059 [13:32<05:47, 15.84it/s]

 70%|█████████████████████████▊           | 12584/18059 [13:36<07:13, 12.64it/s]

 70%|█████████████████████████▊           | 12616/18059 [13:37<05:45, 15.75it/s]

 70%|█████████████████████████▉           | 12648/18059 [13:37<04:10, 21.61it/s]

 70%|█████████████████████████▉           | 12680/18059 [13:38<04:15, 21.08it/s]

 71%|██████████████████████████           | 12744/18059 [13:39<02:39, 33.41it/s]

 71%|██████████████████████████▏          | 12776/18059 [13:46<06:53, 12.76it/s]

 71%|██████████████████████████▏          | 12808/18059 [13:51<08:30, 10.29it/s]

 71%|██████████████████████████▎          | 12840/18059 [13:51<06:16, 13.85it/s]

 71%|██████████████████████████▎          | 12872/18059 [13:52<04:55, 17.55it/s]

 71%|██████████████████████████▍          | 12904/18059 [13:56<07:09, 12.01it/s]

 72%|███████████

 87%|████████████████████████████████▎    | 15784/18059 [17:26<03:14, 11.69it/s]

 88%|████████████████████████████████▍    | 15816/18059 [17:27<02:37, 14.24it/s]

 88%|████████████████████████████████▍    | 15848/18059 [17:28<02:10, 16.97it/s]

 88%|████████████████████████████████▌    | 15880/18059 [17:28<01:33, 23.40it/s]

 88%|████████████████████████████████▌    | 15912/18059 [17:31<02:09, 16.63it/s]

 88%|████████████████████████████████▋    | 15944/18059 [17:33<02:12, 15.97it/s]

 88%|████████████████████████████████▋    | 15976/18059 [17:37<02:38, 13.17it/s]

 89%|████████████████████████████████▊    | 16008/18059 [17:42<03:27,  9.89it/s]

 89%|████████████████████████████████▊    | 16040/18059 [17:43<02:37, 12.83it/s]

 89%|████████████████████████████████▉    | 16072/18059 [17:45<02:34, 12.86it/s]

 89%|████████████████████████████████▉    | 16104/18059 [17:48<02:36, 12.51it/s]

 89%|█████████████████████████████████    | 16136/18059 [17:50<02:20, 13.66it/s]

 90%|███████████

EvaluatorHoldout: Processed 13637 (100.0%) in 9.53 sec. Users per second: 1431
SearchBayesianSkopt: Best config evaluated with evaluator_test with constructor data for final test. Config: {'topK': 266, 'l1_ratio': 0.01, 'alpha': 0.0024936620840052, 'workers': 10} - results:
CUTOFF: 10 - PRECISION: 0.2686881, PRECISION_RECALL_MIN_DEN: 0.2711261, RECALL: 0.0633030, MAP: 0.1445352, MAP_MIN_DEN: 0.1456593, MRR: 0.5271902, NDCG: 0.2839964, F1: 0.1024651, HIT_RATE: 0.9236636, ARHR_ALL_HITS: 0.8651025, NOVELTY: 0.0063742, AVERAGE_POPULARITY: 0.2231689, DIVERSITY_MEAN_INTER_LIST: 0.9824124, DIVERSITY_HERFINDAHL: 0.9982340, COVERAGE_ITEM: 0.2068775, COVERAGE_ITEM_CORRECT: 0.1372723, COVERAGE_USER: 0.9990476, COVERAGE_USER_CORRECT: 0.9227839, DIVERSITY_GINI: 0.0480851, SHANNON_ENTROPY: 10.0739134, RATIO_DIVERSITY_HERFINDAHL: 0.9986194, RATIO_DIVERSITY_GINI: 0.1938686, RATIO_SHANNON_ENTROPY: 0.8130383, RATIO_AVERAGE_POPULARITY: 1.0984065, RATIO_NOVELTY: 0.0282258, 


SearchBayesianSkopt: Saving m

In [ ]:
recommender_new = MultiThreadSLIM_SLIMElasticNetRecommender(URM_train = URM_stacked)
recommender_new.fit(topK=266, l1_ratio=0.01, alpha=0.0024936620840052,workers=10)

SLIMElasticNetRecommender: URM Detected 10245 ( 2.8%) users with no interactions.





  0%|                                                 | 0/18059 [00:00<?, ?it/s]


  0%|                                      | 8/18059 [00:17<11:11:04,  2.23s/it]


  0%|                                      | 40/18059 [00:19<1:52:00,  2.68it/s]


  0%|▏                                       | 72/18059 [00:19<52:07,  5.75it/s]


  1%|▎                                      | 136/18059 [00:19<20:57, 14.25it/s]


  1%|▎                                      | 168/18059 [00:20<14:54, 20.01it/s]


  1%|▍                                      | 200/18059 [00:20<10:45, 27.67it/s]


  1%|▌                                      | 232/18059 [00:21<11:24, 26.04it/s]


  1%|▌                                      | 264/18059 [00:21<08:17, 35.79it/s]


  2%|▋                                      | 320/18059 [00:36<08:15, 35.79it/s]


  2%|▋                                      | 328/18059 [00:36<36:50,  8.02it/s]


  2%|▊                                      | 360/18059 [00:39<32:44,  9.01it/s]


 

 16%|██████                                | 2856/18059 [03:32<08:38, 29.32it/s]


 16%|██████                                | 2888/18059 [03:39<22:42, 11.13it/s]


 16%|██████▏                               | 2920/18059 [03:39<16:10, 15.60it/s]


 16%|██████▏                               | 2952/18059 [03:42<19:05, 13.19it/s]


 17%|██████▎                               | 2984/18059 [03:44<17:29, 14.37it/s]


 17%|██████▎                               | 3016/18059 [03:46<17:40, 14.18it/s]


 17%|██████▍                               | 3048/18059 [03:46<12:46, 19.57it/s]


 17%|██████▍                               | 3080/18059 [03:47<09:28, 26.36it/s]


 17%|██████▌                               | 3112/18059 [03:48<09:43, 25.61it/s]


 17%|██████▌                               | 3144/18059 [03:48<07:06, 35.00it/s]


 18%|██████▋                               | 3176/18059 [03:51<10:52, 22.82it/s]


 18%|██████▊                               | 3208/18059 [03:55<18:42, 13.24it/s]


 18%

 33%|████████████▍                         | 5896/18059 [06:16<10:19, 19.64it/s]


 33%|████████████▍                         | 5928/18059 [06:17<10:07, 19.97it/s]


 33%|████████████▌                         | 5960/18059 [06:18<07:31, 26.81it/s]


 33%|████████████▌                         | 5992/18059 [06:20<09:59, 20.13it/s]


 33%|████████████▋                         | 6024/18059 [06:23<12:15, 16.35it/s]


 34%|████████████▋                         | 6056/18059 [06:25<12:31, 15.97it/s]


 34%|████████████▊                         | 6088/18059 [06:27<11:55, 16.74it/s]


 34%|████████████▉                         | 6120/18059 [06:27<09:16, 21.44it/s]


 34%|████████████▉                         | 6152/18059 [06:30<12:03, 16.46it/s]


 34%|█████████████                         | 6216/18059 [06:32<08:47, 22.43it/s]


 35%|█████████████▏                        | 6248/18059 [06:34<08:59, 21.89it/s]


 35%|█████████████▏                        | 6280/18059 [06:34<07:19, 26.81it/s]


 35%

 49%|██████████████████▍                   | 8776/18059 [08:45<06:18, 24.51it/s]


 49%|██████████████████▌                   | 8808/18059 [08:45<04:53, 31.57it/s]


 49%|██████████████████▌                   | 8840/18059 [08:47<05:12, 29.50it/s]


 49%|██████████████████▋                   | 8872/18059 [08:51<09:57, 15.39it/s]


 49%|██████████████████▋                   | 8904/18059 [08:53<09:44, 15.67it/s]


 49%|██████████████████▊                   | 8936/18059 [08:54<08:32, 17.82it/s]


 50%|██████████████████▊                   | 8968/18059 [08:56<08:09, 18.56it/s]


 50%|██████████████████▉                   | 9000/18059 [08:57<08:02, 18.78it/s]


 50%|███████████████████                   | 9032/18059 [09:01<10:04, 14.93it/s]


 50%|███████████████████                   | 9064/18059 [09:02<08:18, 18.05it/s]


 50%|███████████████████▏                  | 9096/18059 [09:02<06:09, 24.25it/s]


 51%|███████████████████▏                  | 9128/18059 [09:04<06:45, 22.04it/s]


 51%

In [ ]:
submission=create_submission(recommender_new)
write_submission(submission,"SLIME_LongTail")